In [7]:
import json
import time
import pickle
import glob, os    
import pandas as pd
from tqdm import tqdm
from os import path as PATH

import torch
from kiwipiepy import Kiwi
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

# 질병관리본부 데이터

corpus : 의도와 화자가 labeling된 데이터
```python
{"발화내용" : {"Q":{"고객": set(), "상담사": set()},
                      "A":{"고객": set(), "상담사": set()} }}
```

In [12]:
if PATH.exists("/workspace/data/public_dataset"):
    with open("/workspace/data/public_dataset", "rb") as f:
        dataset = pickle.load(f)

corpus = list(dataset.keys())
corpus

['열이 나는데 코로나일까요?',
 '네. 안녕하세요.',
 '열 말고 다른 증상은 없으신가요?',
 '기침도 조금 나오는 거 같아요.',
 '콧물이나 코막힘 증상은요?',
 '콧물은 안나와요.',
 '열나고 기침나면 코로나에 걸린 거예요?',
 '코로나19의 가장 흔한 증상은 발열, 마른 기침, 피로이며 그 외에 후각 및 미각 소실, 근육통, 인후통, 콧물, 코막힘, 두통, 결막염, 설사, 피부 증상 등 다양한 증상이 나타날 수 있습니다.',
 '설사가 나도 코로나일 수 있다구요?',
 '네, 설사도 증상의 한 종류입니다.',
 '감기 증상이랑 똑같네요?',
 '감기 증상과 비슷합니다.',
 '감기랑 어떻게 구별해요?',
 '증상만으로는 구별이 어려우므로 일단, 확진자와 접촉했을 경우나 주변에 코로나 확진자가 있을 경우 검사 받으시기를 권해드립니다.',
 '텔레비전에서 보니까 막 엄청 아파보이던데, 걸리면 많이 아파요?',
 '이러한 증상은 보통 경미하고 점진적으로 나타납니다. 어떤 사람들은 감염되어도 매우 약한 증상만 나타날 수 있습니다.',
 '진짜 헷갈리네요.',
 '무증상환자는 뭐예요?',
 '아무런 증상이 없고 건강 상태도 나쁘지 않은데, 진단 검사만 하면 계속 양성이 나오면 무증상 환자입니다.',
 '열도 안나고 하나도 안아프다고요?',
 '네, 맞습니다.',
 '무증상인데 환자인줄 어떻게 알아요?',
 '증상이 없다 하더라도 검사를 통해 알 수 있습니다.',
 '검사 안하면 모르는 거 맞죠?',
 '그렇습니다.',
 '무증상 환자도 코로나 전염시켜요?',
 '네, 무증상 환자도 전염시킵니다.',
 '기침도 안할텐데 어떻게 전염이 돼요?',
 '무증상 환자들이 기침하거나 침을 뱉어도 침이나 가래 방울을 통하여 코로나를 전파시킬 수 있습니다.',
 '그럼 격리시켜야 되는 거 아니에요?',
 '무증상 환자가 아무런 증상이 없다 하더라도 격리 조치를 합니다.',
 '무증상 환자가 더 무서운 거네요?',
 '코로나19 무증상 환자 전파력 얕봐선 안 됩니다

In [13]:
len(corpus)

63283

빈 문자열이거나 숫자로만 이루어진 줄은 제외


In [14]:
preprocessed_documents = list()
for sentence in tqdm(corpus):
    if sentence and not sentence.replace(' ','').isdecimal():
        preprocessed_documents.append(sentence)

100%|██████████| 63283/63283 [00:00<00:00, 1515415.98it/s]


In [15]:
len(preprocessed_documents)

63280

In [28]:
print(preprocessed_documents)

['열이 나는데 코로나일까요?', '네. 안녕하세요.', '열 말고 다른 증상은 없으신가요?', '기침도 조금 나오는 거 같아요.', '콧물이나 코막힘 증상은요?', '콧물은 안나와요.', '열나고 기침나면 코로나에 걸린 거예요?', '코로나19의 가장 흔한 증상은 발열, 마른 기침, 피로이며 그 외에 후각 및 미각 소실, 근육통, 인후통, 콧물, 코막힘, 두통, 결막염, 설사, 피부 증상 등 다양한 증상이 나타날 수 있습니다.', '설사가 나도 코로나일 수 있다구요?', '네, 설사도 증상의 한 종류입니다.', '감기 증상이랑 똑같네요?', '감기 증상과 비슷합니다.', '감기랑 어떻게 구별해요?', '증상만으로는 구별이 어려우므로 일단, 확진자와 접촉했을 경우나 주변에 코로나 확진자가 있을 경우 검사 받으시기를 권해드립니다.', '텔레비전에서 보니까 막 엄청 아파보이던데, 걸리면 많이 아파요?', '이러한 증상은 보통 경미하고 점진적으로 나타납니다. 어떤 사람들은 감염되어도 매우 약한 증상만 나타날 수 있습니다.', '진짜 헷갈리네요.', '무증상환자는 뭐예요?', '아무런 증상이 없고 건강 상태도 나쁘지 않은데, 진단 검사만 하면 계속 양성이 나오면 무증상 환자입니다.', '열도 안나고 하나도 안아프다고요?', '네, 맞습니다.', '무증상인데 환자인줄 어떻게 알아요?', '증상이 없다 하더라도 검사를 통해 알 수 있습니다.', '검사 안하면 모르는 거 맞죠?', '그렇습니다.', '무증상 환자도 코로나 전염시켜요?', '네, 무증상 환자도 전염시킵니다.', '기침도 안할텐데 어떻게 전염이 돼요?', '무증상 환자들이 기침하거나 침을 뱉어도 침이나 가래 방울을 통하여 코로나를 전파시킬 수 있습니다.', '그럼 격리시켜야 되는 거 아니에요?', '무증상 환자가 아무런 증상이 없다 하더라도 격리 조치를 합니다.', '무증상 환자가 더 무서운 거네요?', '코로나19 무증상 환자 전파력 얕봐선 안 됩니다. 무증상 감염이 코로나19를 퍼뜨리는 데 중요한 역할을 

## Mecab과 Sbert를 이용한 bertopic

In [3]:
user_stop_word = ['안녕', '안녕하세요', '안녕하십니까', '때문', '지금', '아까', '전화', '감사', '성함', '정도', '개월', \
    '하루', '이틀', '보름', '이내', '어제', '오늘', '아침', '저녁', '.', '네', '네네', '네네네']
extract_pos_list = ['NNG', 'NNP', 'NNB', 'NR', 'NP']

class CustomTokenizer:
    def __init__(self, kiwi):
        self.kiwi = kiwi
    def __call__(self, text):      
        result = []
        for word in self.kiwi.tokenize(text):
            if word[1] in extract_pos_list and len(word[0]) > 1 and word[0] not in user_stop_word:
                result.append(word[0])

        return result

In [4]:
custom_tokenizer = CustomTokenizer(Kiwi())

In [8]:
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)

In [9]:
model = BERTopic(embedding_model="sentence-transformers/xlm-r-100langs-bert-base-nli-stsb-mean-tokens", \
                             vectorizer_model=vectorizer,
                             nr_topics=10,
                             top_n_words=10,
                             calculate_probabilities=True)

In [16]:
import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"

import time

start = time.time()
topics, probs = model.fit_transform(preprocessed_documents[:10000])
end = time.time()

print(f"{end - start:.5f} sec")

76.75584 sec


In [17]:
model.get_topic_info()

Topic  Count             Name
0      -1   7001  -1_검사_코로나_증상_가능
1       0    479   0_해외_확진자_여행_최근
2       1    431    1_비용_얼마_시간_결과
3       2    381   2_증상_감기_코로나_가족
4       3    343   3_기침_발열_증상_호흡기
5       4    270   4_어디_지역_진료소_선별
6       5    257    5_말씀_처벌_정보_유출
7       6    220  6_질환_흡연자_기저_후유증
8       7    219    7_서울_대전_병원_세종
9       8    202    8_수고_다행_답변_친절
10      9    197    9_사항_질문_무엇_문의

In [16]:
model.visualize_topics()

In [24]:
model.visualize_distribution(probs[10])

In [26]:
probs.shape

(63280, 50)

In [27]:
for i in range(0, 50):
  print(i,'번째 토픽 :', model.get_topic(i))

0 번째 토픽 : [('진료소', 0.08264434980982828), ('선별', 0.07971847167528226), ('보건소', 0.07030031252823085), ('병원', 0.04786661308124194), ('가까운', 0.03748482901390062), ('방문', 0.02896121402041508), ('환자', 0.02860497170722009), ('관할', 0.028344488798931103), ('에서', 0.02617654606885898), ('의료', 0.025003654075452738)]
1 번째 토픽 : [('추석', 0.037556376336247366), ('는데', 0.03628866919827707), ('동선', 0.03614548427134268), ('겹치', 0.033594243424726805), ('그럼', 0.026222968518838263), ('아니', 0.02558953368065251), ('확진', 0.022880842829132872), ('네요', 0.021086394492200667), ('던데', 0.0205885540988663), ('아닌가요', 0.02002553646488729)]
2 번째 토픽 : [('확진', 0.059615117916558935), ('오늘', 0.04567561424817463), ('105', 0.043836025745793504), ('인가요', 0.041689122181077815), ('입니다', 0.0336322706410536), ('예약', 0.03304912981720283), ('날짜', 0.03155270513632279), ('서구', 0.029405393476494464), ('해제', 0.025250347599111374), ('누적', 0.024844179068023733)]
3 번째 토픽 : [('증상', 0.09899801444515266), ('어떤', 0.0917178036117005), ('궁금', 0.0

# Whisper data

In [4]:
file = "/app/whisper_text_merged/녹취_4574_인"
with open(file, "rb") as f:
    whisper_4574_in_corpus = pickle.load(f)

len(whisper_4574_in_corpus)

22761

In [5]:
preprocessed_documents = list()
for sentence in tqdm(whisper_4574_in_corpus):
    if sentence and not sentence.replace(' ','').isdecimal():
        preprocessed_documents.append(sentence)
len(preprocessed_documents)

100%|██████████| 22761/22761 [00:00<00:00, 1431840.80it/s]


22693

In [6]:
word_list = pd.read_csv('./data/word_dict.csv')['word'].tolist()
word_list

['강남지인병원',
 '스트레스',
 '정신건강의학과',
 '미역',
 '실제',
 '오사카',
 '안양초등학교',
 '음성',
 '질투',
 '옆집',
 '대장내시경',
 '점막',
 '발병',
 '교장',
 '임원',
 '연관',
 '국립',
 '정진',
 '일부',
 '가위',
 '칼슘',
 '대진',
 '정성',
 '쿠팡',
 '오프',
 '상복부',
 '생명',
 '신경외과',
 '비타민',
 '인구',
 '손바닥',
 '할아버지',
 '당첨',
 '탈출',
 '동해',
 '뒤끝',
 '책장',
 '오스템임플란트',
 '의원',
 '직업',
 '민감',
 '두개골',
 '강북삼성병원',
 '주인',
 '밥상',
 '건강보험적용',
 '구리시',
 '예년',
 '자택',
 '감마나이프',
 '스트레칭',
 '여인',
 '아델',
 '언급',
 '시간표',
 '치킨',
 '암호',
 '요약',
 '팔뚝',
 '샤워',
 '수미',
 '골밀도검사',
 '전방',
 '건강보험',
 '호흡기질환',
 '병점',
 '분변',
 '보충',
 '흉터',
 '삼성',
 '실손',
 '평은초등학교',
 '발달',
 '화목',
 '청담동',
 '한림병원',
 '일치',
 '탄력',
 '부민',
 '신림동',
 '송림',
 '중반',
 '오금초등학교',
 '밴드',
 '동원',
 '분실',
 '경치',
 '결론',
 '비서',
 '된장',
 '괴사',
 '흥국생명',
 '은희',
 '수축',
 '은혜',
 '마비',
 '그림',
 '고속',
 '방배동',
 '찜질',
 '화곡동',
 '어미',
 '고려대',
 '적립',
 '계통',
 '면적',
 '회신',
 '봉생병원',
 '시즌',
 '건담',
 '무료',
 '방전',
 '고신대학교',
 '호흡증',
 '기원',
 '작성',
 '유니버셜',
 '뇌경색',
 '호소',
 '성격',
 '탈수',
 '약화',
 '부민병원',
 '일상',
 '월경',
 '맥스',
 '이화여자대학교',
 '기력',
 '신곡',
 '전공',
 '

In [9]:
stopword = []
with open('../data/stopword.txt', 'r', encoding='utf-8') as f:
    for line in f:
        stopword.append(line.rstrip('\n'))
stopword = stopword[1:]

In [10]:
user_stop_word = ['안녕', '안녕하세요', '안녕하십니까', '때문', '지금', '아까', '전화', '감사', '성함', '정도',
                 '개월', '하루', '이틀', '보름', '이내', '어제', '오늘', '아침', '저녁', '.', '네', '네네', '네네네']
stopword.extend(user_stop_word)

In [11]:
# 형태소 품사 태깅 : 일반명사, 고유명사, 의존명사, 수사, 대명사 (체언 리스트)
# http://kkma.snu.ac.kr/documents/?doc=postag 참고
extract_pos_list = ['NNG', 'NNP', 'NNB', 'NR', 'NP']

class CustomTokenizer:
    def __init__(self, kiwi):
        self.kiwi = kiwi
    def __call__(self, text):      
        result = []
        for word in word_list:
            # kiwi 모델에 사용자 정의 형태소 추가 
            self.kiwi.add_user_word(word, 'NNG')

        for word in self.kiwi.tokenize(text):
            if word[1] in extract_pos_list and len(word[0]) > 1 and word[0] not in stopword:
                result.append(word[0])

        return result

In [12]:
from konlpy.tag import Mecab
from sklearn.feature_extraction.text import CountVectorizer

custom_tokenizer = CustomTokenizer(Kiwi(model_type='sbg', typos='basic', num_workers=4))
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)

In [13]:
model = BERTopic(embedding_model="/workspace/data/ko-sroberta-multitask", \
                             vectorizer_model=vectorizer,
                             calculate_probabilities=True)

In [14]:
import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"

import time

start = time.time()
topics, probs = model.fit_transform(preprocessed_documents)
end = time.time()

print(f"{end - start:.5f} sec")

259.59920 sec


In [20]:
import csv

model.get_topic_info().to_csv("filename.csv", mode='w')

# 통합데이터 + Whisper BERTopic

In [2]:
corpus_list = pd.read_csv('/workspace/data/all_aihub_sentence.csv', sep=',')['sentence'].tolist()
len(corpus_list)

102136

In [3]:
preprocessed_corpus = []
for sentence in tqdm(corpus_list):
    sentence = str(sentence)
    if sentence and not sentence.replace(' ','').isdecimal():
        preprocessed_corpus.append(sentence)
len(preprocessed_corpus)

100%|██████████| 102136/102136 [00:00<00:00, 1273956.21it/s]


102134

In [31]:
stopword = []
with open('/workspace/data/stopword.txt', 'r', encoding='utf-8') as f:
    for line in f:
        stopword.append(line.rstrip('\n'))
stopword = stopword[1:]

In [32]:
user_stop_word = ['안녕', '안녕하세요', '안녕하십니까', '때문', '지금', '아까', '전화', '감사', '성함', '정도',
                 '개월', '하루', '이틀', '보름', '이내', '어제', '오늘', '아침', '저녁', '0', 'O', 'o', '.', '아', '네', '네네', '네네네']
stopword.extend(user_stop_word)

In [33]:
from sklearn.feature_extraction.text import CountVectorizer

extract_pos_list = ['NNG', 'NNP', 'NNB', 'NR', 'NP']

class CustomTokenizer:
    def __init__(self, kiwi):
        self.kiwi = kiwi
    def __call__(self, text):      
        result = []
        for word in word_list:
            self.kiwi.add_user_word(word, 'NNG')

        for word in self.kiwi.tokenize(text):
            if word[1] in extract_pos_list and len(word[0]) > 1 and word[0] not in stopword:
                result.append(word[0])

        return result

In [34]:
custom_tokenizer = CustomTokenizer(Kiwi(model_type='sbg', typos='basic', num_workers=4))
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)

In [ ]:
os.environ["TOKENIZERS_PARALLELISM"] = "false"

topic_model = BERTopic(embedding_model="/workspace/data/ko-sroberta-multitask", \
                             vectorizer_model=vectorizer,
                             nr_topics=10,
                             top_n_words=10,
                             calculate_probabilities=True)


start = time.time()
topics, probs = topic_model.fit_transform(preprocessed_corpus)
end = time.time()

print(f"{end - start:.5f} sec")

2023-02-07 03:17:55,894 - BERTopic - Transformed documents to Embeddings


In [ ]:
with open("corpus_topic", "rb") as ft:
    topic = pickle.load(ft)
with open("corpus_probs", "rb") as fp:
    probs = pickle.load(fp)
with open("corpus_weight", "rb") as fp:
    topic_model = pickle.load(fp)

In [7]:
with open("corpus_topic", "wb") as ft:
    pickle.dump(topics, ft)
with open("corpus_probs", "wb") as fp:
    pickle.dump(probs, fp)
with open("corpus_weight", "wb") as fw:
    pickle.dump(topic_model, fw)

In [19]:
topic_model.get_topic(1)

[('학교', 0.020379953083224513),
 ('학원', 0.015838518047934427),
 ('학교에서', 0.014147166952027985),
 ('초등학교', 0.014078843672784211),
 ('학원은', 0.013112409759017701),
 ('학원에서', 0.012782358110587526),
 ('학교에', 0.012260583530206275),
 ('학교는', 0.011498709133683893),
 ('수업을', 0.01141708717662209),
 ('유치원', 0.010728335257378119)]

`get_topic_info()`: 생성된 topic을 빈도순으로 볼 수 있음

# Visualization

PLDAVIS와 비슷한 형태로 시각화

In [13]:
topic_model.visualize_hierarchy(top_n_topics=50)